In [0]:
####### Creación de un DATAFRAME DE PRUEBA #######


# Verificar versión de Spark
print(spark.version)

# Crear un DataFrame de prueba
data = [(1, "Test"), (2, "Cluster"), (3, "Working")]
df = spark.createDataFrame(data, ["id", "message"])
df.show()


4.0.0
+---+-------+
| id|message|
+---+-------+
|  1|   Test|
|  2|Cluster|
|  3|Working|
+---+-------+



In [0]:
%sql
-- ============================================================================
-- PASO 1: Crear el Catálogo (Catalog)
-- ============================================================================
CREATE CATALOG IF NOT EXISTS heart_disease_catalog
COMMENT 'Catálogo para análisis de salud cardiovascular y factores de riesgo';

-- Usar el catálogo creado
USE CATALOG heart_disease_catalog;

-- ============================================================================
-- PASO 2: Crear el Schema
-- ============================================================================
CREATE SCHEMA IF NOT EXISTS heart2020_schema
COMMENT 'Schema para dataset Heart Disease 2020 - CDC BRFSS'
WITH DBPROPERTIES (
    'project' = 'heart_disease_analysis',
    'dataset_year' = '2020',
    'source' = 'CDC_BRFSS',
    'created_by' = 'Jonathan Alvarez',
    'version' = '1.0'
);


-- ============================================================================
-- PASO 3: Crear las Tablas (Tables)
-- ============================================================================

-- Tabla: persona
-- Nombre completo: heart_disease_catalog.heart2020_schema.persona
-- Descripción: Almacena información demográfica y de salud general
CREATE TABLE IF NOT EXISTS heart_disease_catalog.heart2020_schema.persona (
    id_persona      INT NOT NULL COMMENT 'Identificador único de la persona',
    Sex             STRING COMMENT 'Sexo de la persona (Male/Female)',
    AgeCategory     STRING COMMENT 'Categoría de edad',
    Race            STRING COMMENT 'Raza/Etnia de la persona',
    BMI             DOUBLE COMMENT 'Índice de Masa Corporal',
    SleepTime       DOUBLE COMMENT 'Horas promedio de sueño por día',
    GenHealth       STRING COMMENT 'Estado general de salud',
    PhysicalHealth  DOUBLE COMMENT 'Días con mala salud física (últimos 30 días)',
    MentalHealth    DOUBLE COMMENT 'Días con mala salud mental (últimos 30 días)',
    DiffWalking     STRING COMMENT 'Dificultad para caminar (Yes/No)',
    CONSTRAINT pk_persona PRIMARY KEY (id_persona)
)
USING DELTA;

-- Tabla: habitos
-- Nombre completo: heart_disease_catalog.heart2020_schema.habitos
-- Descripción: Almacena información sobre hábitos y estilo de vida
CREATE TABLE IF NOT EXISTS heart_disease_catalog.heart2020_schema.habitos (
    id_habito        INT NOT NULL COMMENT 'Identificador único del registro de hábitos',
    Smoking          STRING COMMENT 'Ha fumado al menos 100 cigarrillos (Yes/No)',
    AlcoholDrinking  STRING COMMENT 'Consumo excesivo de alcohol (Yes/No)',
    PhysicalActivity STRING COMMENT 'Actividad física últimos 30 días (Yes/No)',
    Diabetic         STRING COMMENT 'Estado diabético',
    id_persona       INT COMMENT 'Referencia a la persona',
    CONSTRAINT pk_habito PRIMARY KEY (id_habito),
    CONSTRAINT fk_habito_persona FOREIGN KEY (id_persona) 
        REFERENCES heart_disease_catalog.heart2020_schema.persona(id_persona)
)
USING DELTA;

-- Tabla: condiciones_medicas
-- Nombre completo: heart_disease_catalog.heart2020_schema.condiciones_medicas
-- Descripción: Almacena información sobre condiciones médicas preexistentes
CREATE TABLE IF NOT EXISTS heart_disease_catalog.heart2020_schema.condiciones_medicas (
    id_condicion  INT NOT NULL COMMENT 'Identificador único del registro de condiciones',
    Stroke        STRING COMMENT 'Ha tenido derrame cerebral (Yes/No)',
    Asthma        STRING COMMENT 'Tiene asma (Yes/No)',
    KidneyDisease STRING COMMENT 'Tiene enfermedad renal (Yes/No)',
    SkinCancer    STRING COMMENT 'Tiene cáncer de piel (Yes/No)',
    id_persona    INT COMMENT 'Referencia a la persona',
    CONSTRAINT pk_condicion PRIMARY KEY (id_condicion),
    CONSTRAINT fk_condicion_persona FOREIGN KEY (id_persona) 
        REFERENCES heart_disease_catalog.heart2020_schema.persona(id_persona)
)
USING DELTA;

-- Tabla: salud_cardiaca
-- Nombre completo: heart_disease_catalog.heart2020_schema.salud_cardiaca
-- Descripción: Almacena información específica sobre enfermedades cardíacas
CREATE TABLE IF NOT EXISTS heart_disease_catalog.heart2020_schema.salud_cardiaca (
    id_saludcardiaca INT NOT NULL COMMENT 'Identificador único del registro de salud cardíaca',
    HeartDisease     STRING COMMENT 'Tiene enfermedad cardíaca (Yes/No)',
    id_persona       INT COMMENT 'Referencia a la persona',
    CONSTRAINT pk_saludcardiaca PRIMARY KEY (id_saludcardiaca),
    CONSTRAINT fk_saludcardiaca_persona FOREIGN KEY (id_persona) 
        REFERENCES heart_disease_catalog.heart2020_schema.persona(id_persona)
)
USING DELTA

In [0]:
%sql
DESCRIBE TABLE heart_disease_catalog.heart2020_schema.persona;



col_name data_type comment id_persona int Identificador único de la persona Sex string Sexo de la persona (Male/Female) AgeCategory string Categoría de edad Race string Raza/Etnia de la persona BMI double Índice de Masa Corporal SleepTime double Horas promedio de sueño por día GenHealth string Estado general de salud PhysicalHealth double Días con mala salud física (últimos 30 días) MentalHealth double Días con mala salud mental (últimos 30 días) DiffWalking string Dificultad para caminar (Yes/No)

In [0]:
%sql
DESCRIBE TABLE heart_disease_catalog.heart2020_schema.habitos;


col_name data_type comment id_habito int Identificador único del registro de hábitos Smoking string Ha fumado al menos 100 cigarrillos (Yes/No) AlcoholDrinking string Consumo excesivo de alcohol (Yes/No) PhysicalActivity string Actividad física últimos 30 días (Yes/No) Diabetic string Estado diabético id_persona int Referencia a la persona

In [0]:
%sql
    
DESCRIBE TABLE heart_disease_catalog.heart2020_schema.condiciones_medicas;
    


col_name data_type comment id_condicion int Identificador único del registro de condiciones Stroke string Ha tenido derrame cerebral (Yes/No) Asthma string Tiene asma (Yes/No) KidneyDisease string Tiene enfermedad renal (Yes/No) SkinCancer string Tiene cáncer de piel (Yes/No) id_persona int Referencia a la persona

In [0]:
%sql
DESCRIBE TABLE heart_disease_catalog.heart2020_schema.salud_cardiaca;

col_name data_type comment id_saludcardiaca int Identificador único del registro de salud cardíaca HeartDisease string Tiene enfermedad cardíaca (Yes/No) id_persona int Referencia a la persona

In [0]:

!pip install kagglehub[pandas-datasets]>=0.3.8

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
import kagglehub

# Descargar el dataset desde Kaggle
path = kagglehub.dataset_download("kamilpytlak/personal-key-indicators-of-heart-disease")

print("Path to dataset files:", path)


Path to dataset files: /home/spark-25118b71-df92-45cb-bd69-5d/.cache/kagglehub/datasets/kamilpytlak/personal-key-indicators-of-heart-disease/versions/6


In [0]:
from pyspark.sql.types import StructType, StructField, StringType, DoubleType, IntegerType

# Esquema del CSV original de Heart Disease 2020
schema_original = StructType([
    # Enfermedad cardíaca (objetivo)
    StructField("HeartDisease", StringType(), False),
    
    # Información demográfica y salud
    StructField("BMI", DoubleType(), False),
    StructField("Smoking", StringType(), False),
    StructField("AlcoholDrinking", StringType(), False),
    StructField("Stroke", StringType(), False),
    StructField("PhysicalHealth", IntegerType(), False),
    StructField("MentalHealth", IntegerType(), False),
    StructField("DiffWalking", StringType(), False),
    
    # Datos personales
    StructField("Sex", StringType(), False),
    StructField("AgeCategory", StringType(), False),
    StructField("Race", StringType(), False),
    
    # Condiciones médicas
    StructField("Diabetic", StringType(), False),
    StructField("PhysicalActivity", StringType(), False),
    StructField("GenHealth", StringType(), False),
    StructField("SleepTime", IntegerType(), False),
    StructField("Asthma", StringType(), False),
    StructField("KidneyDisease", StringType(), False),
    StructField("SkinCancer", StringType(), False)
])

print("Esquema definido con", len(schema_original.fields), "campos")

Esquema definido con 18 campos


In [0]:
import os
import zipfile
import glob
import pandas as pd

data_path = path 
print("Ruta base:", data_path)

# Si es un ZIP, lo extraemos; si es una carpeta, la usamos directo
if os.path.isdir(data_path):
    # Ya es una carpeta
    root = data_path
    print("Es un directorio, no ZIP.")
elif zipfile.is_zipfile(data_path):
    # Es un ZIP:
    root = "/tmp/heart_disease_dataset"
    print("Es un ZIP, extrayendo en:", root)
    with zipfile.ZipFile(data_path, "r") as z:
        z.extractall(root)
else:
    raise ValueError(f"No es ni carpeta ni ZIP válido: {data_path}")

# Buscar TODOS los CSV dentro de TODAS las subcarpetas
csv_files = glob.glob(os.path.join(root, "**", "*.csv"), recursive=True)
print("CSV encontrados:", csv_files)

if not csv_files:
    raise FileNotFoundError("No se encontró ningún archivo CSV en el dataset.")



Ruta base: /home/spark-25118b71-df92-45cb-bd69-5d/.cache/kagglehub/datasets/kamilpytlak/personal-key-indicators-of-heart-disease/versions/6
Es un directorio, no ZIP.
CSV encontrados: ['/home/spark-25118b71-df92-45cb-bd69-5d/.cache/kagglehub/datasets/kamilpytlak/personal-key-indicators-of-heart-disease/versions/6/2020/heart_2020_cleaned.csv', '/home/spark-25118b71-df92-45cb-bd69-5d/.cache/kagglehub/datasets/kamilpytlak/personal-key-indicators-of-heart-disease/versions/6/2022/heart_2022_no_nans.csv', '/home/spark-25118b71-df92-45cb-bd69-5d/.cache/kagglehub/datasets/kamilpytlak/personal-key-indicators-of-heart-disease/versions/6/2022/heart_2022_with_nans.csv']


In [0]:
# 3. Leer DF de las subcarpetas
df2020 = pd.read_csv(csv_files[0])
df2022 = pd.read_csv(csv_files[1])
display(df2020.head())
display(df2022.head())


HeartDisease BMI Smoking AlcoholDrinking Stroke PhysicalHealth MentalHealth DiffWalking Sex AgeCategory Race Diabetic PhysicalActivity GenHealth SleepTime Asthma KidneyDisease SkinCancer No 16.6 Yes No No 3.0 30.0 No Female 55-59 White Yes Yes Very good 5.0 Yes No Yes No 20.34 No No Yes 0.0 0.0 No Female 80 or older White No Yes Very good 7.0 No No No No 26.58 Yes No No 20.0 30.0 No Male 65-69 White Yes Yes Fair 8.0 Yes No No No 24.21 No No No 0.0 0.0 No Female 75-79 White No No Good 6.0 No No Yes No 23.71 No No No 28.0 0.0 Yes Female 40-44 White No Yes Very good 8.0 No No No

State Sex GeneralHealth PhysicalHealthDays MentalHealthDays LastCheckupTime PhysicalActivities SleepHours RemovedTeeth HadHeartAttack HadAngina HadStroke HadAsthma HadSkinCancer HadCOPD HadDepressiveDisorder HadKidneyDisease HadArthritis HadDiabetes DeafOrHardOfHearing BlindOrVisionDifficulty DifficultyConcentrating DifficultyWalking DifficultyDressingBathing DifficultyErrands SmokerStatus ECigaretteUsage ChestScan RaceEthnicityCategory AgeCategory HeightInMeters WeightInKilograms BMI AlcoholDrinkers HIVTesting FluVaxLast12 PneumoVaxEver TetanusLast10Tdap HighRiskLastYear CovidPos Alabama Female Very good 4.0 0.0 Within past year (anytime less than 12 months ago) Yes 9.0 None of them No No No No No No No No Yes No No No No No No No Former smoker Never used e-cigarettes in my entire life No White only, Non-Hispanic Age 65 to 69 1.6 71.67 27.99 No No Yes Yes Yes, received Tdap No No Alabama Male Very good 0.0 0.0 Within past year (anytime less than 12 months ago) Yes 6.0 None of them No No No No No No No No Yes Yes No No No No No No Former smoker Never used e-cigarettes in my entire life No White only, Non-Hispanic Age 70 to 74 1.78 95.25 30.13 No No Yes Yes Yes, received tetanus shot but not sure what type No No Alabama Male Very good 0.0 0.0 Within past year (anytime less than 12 months ago) No 8.0 6 or more, but not all No No No No No No No No Yes No No Yes No Yes No No Former smoker Never used e-cigarettes in my entire life Yes White only, Non-Hispanic Age 75 to 79 1.85 108.86 31.66 Yes No No Yes No, did not receive any tetanus shot in the past 10 years No Yes Alabama Female Fair 5.0 0.0 Within past year (anytime less than 12 months ago) Yes 9.0 None of them No No No No Yes No Yes No Yes No No No No Yes No No Never smoked Never used e-cigarettes in my entire life No White only, Non-Hispanic Age 80 or older 1.7 90.72 31.32 No No Yes Yes No, did not receive any tetanus shot in the past 10 years No Yes Alabama Female Good 3.0 15.0 Within past year (anytime less than 12 months ago) Yes 5.0 1 to 5 No No No No No No No No Yes No No No No No No No Never smoked Never used e-cigarettes in my entire life No White only, Non-Hispanic Age 80 or older 1.55 79.38 33.07 No No Yes Yes No, did not receive any tetanus shot in the past 10 years No No

In [0]:
spark_df = spark.createDataFrame(df2020)




In [0]:
spark_df = spark.createDataFrame(df2020)

In [0]:
# Creamos una tabla temporal llamada "heart_2020_cleaned"

spark_df.createTempView("heart_2020_cleaned")
display(spark_df)
     

HeartDisease BMI Smoking AlcoholDrinking Stroke PhysicalHealth MentalHealth DiffWalking Sex AgeCategory Race Diabetic PhysicalActivity GenHealth SleepTime Asthma KidneyDisease SkinCancer No 16.6 Yes No No 3.0 30.0 No Female 55-59 White Yes Yes Very good 5.0 Yes No Yes No 20.34 No No Yes 0.0 0.0 No Female 80 or older White No Yes Very good 7.0 No No No No 26.58 Yes No No 20.0 30.0 No Male 65-69 White Yes Yes Fair 8.0 Yes No No No 24.21 No No No 0.0 0.0 No Female 75-79 White No No Good 6.0 No No Yes No 23.71 No No No 28.0 0.0 Yes Female 40-44 White No Yes Very good 8.0 No No No Yes 28.87 Yes No No 6.0 0.0 Yes Female 75-79 Black No No Fair 12.0 No No No No 21.63 No No No 15.0 0.0 No Female 70-74 White No Yes Fair 4.0 Yes No Yes No 31.64 Yes No No 5.0 0.0 Yes Female 80 or older White Yes No Good 9.0 Yes No No No 26.45 No No No 0.0 0.0 No Female 80 or older White No, borderline diabetes No Fair 5.0 No Yes No No 40.69 No No No 0.0 0.0 Yes Male 65-69 White No Yes Good 10.0 No No No Yes 34.3 Yes No No 30.0 0.0 Yes Male 60-64 White Yes No Poor 15.0 Yes No No No 28.71 Yes No No 0.0 0.0 No Female 55-59 White No Yes Very good 5.0 No No No No 28.37 Yes No No 0.0 0.0 Yes Male 75-79 White Yes Yes Very good 8.0 No No No No 28.15 No No No 7.0 0.0 Yes Female 80 or older White No No Good 7.0 No No No No 29.29 Yes No No 0.0 30.0 Yes Female 60-64 White No No Good 5.0 No No No No 29.18 No No No 1.0 0.0 No Female 50-54 White No Yes Very good 6.0 No No No No 26.26 No No No 5.0 2.0 No Female 70-74 White No No Very good 10.0 No No No No 22.59 Yes No No 0.0 30.0 Yes Male 70-74 White No, borderline diabetes Yes Good 8.0 No No No No 29.86 Yes No No 0.0 0.0 Yes Female 75-79 Black Yes No Fair 5.0 No Yes No No 18.13 No No No 0.0 0.0 No Male 80 or older White No Yes Excellent 8.0 No No Yes No 21.16 No No No 0.0 0.0 No Female 80 or older Black No, borderline diabetes No Good 8.0 No No No No 28.9 No No No 2.0 5.0 No Female 70-74 White Yes No Very good 7.0 No No No No 26.17 Yes No No 0.0 15.0 No Female 45-49 White No Yes Very good 6.0 No No No No 25.82 Yes No No 0.0 30.0 No Male 80 or older White Yes Yes Fair 8.0 No No No No 25.75 No No No 0.0 0.0 No Female 80 or older White No Yes Very good 6.0 No No Yes No 29.18 Yes No No 30.0 30.0 Yes Female 60-64 White No No Poor 6.0 Yes No No No 34.34 Yes No No 21.0 8.0 Yes Female 65-69 White No Yes Fair 9.0 No No No No 31.66 Yes No No 5.0 0.0 No Male 60-64 White No Yes Very good 5.0 No No No No 24.89 No No No 1.0 0.0 No Female 55-59 White No Yes Very good 7.0 No No No No 36.58 No No No 0.0 0.0 No Female 60-64 White Yes No Good 5.0 No No Yes No 25.84 Yes No No 5.0 0.0 No Male 70-74 Black No Yes Good 8.0 No No No No 30.67 No No No 4.0 4.0 Yes Female 80 or older White No Yes Fair 8.0 Yes No No No 45.35 No No No 30.0 0.0 Yes Male 70-74 White Yes No Good 8.0 No No No No 19.02 Yes No No 0.0 5.0 No Female 60-64 White No Yes Very good 9.0 No No No No 38.97 No No No 0.0 0.0 Yes Female 70-74 Black No No Good 6.0 No No No Yes 32.98 Yes No Yes 10.0 0.0 Yes Male 75-79 White Yes Yes Poor 4.0 No No Yes No 24.62 No No No 5.0 0.0 No Female 80 or older White No Yes Good 6.0 No No No No 20.43 Yes No No 3.0 3.0 No Female 65-69 White No Yes Fair 5.0 Yes No Yes No 27.37 Yes No No 0.0 0.0 No Female 80 or older White No No Very good 8.0 No No No No 21.93 No No No 3.0 2.0 No Female 70-74 Black No Yes Fair 4.0 No Yes No No 22.6 Yes No Yes 0.0 10.0 No Female 55-59 White No No Very good 8.0 No No No No 28.13 No No No 0.0 0.0 No Male 60-64 White No Yes Excellent 8.0 No No No Yes 25.06 No No No 0.0 0.0 Yes Female 80 or older White Yes No Good 7.0 No No Yes Yes 30.23 Yes No No 6.0 2.0 Yes Female 75-79 White Yes Yes Fair 8.0 No Yes No No 30.34 Yes No No 30.0 10.0 Yes Male 55-59 White No, borderline diabetes No Fair 6.0 No No No Yes 20.37 Yes No No 3.0 0.0 No Female 70-74 White No No Poor 10.0 No No No No 33.23 No No No 0.0 0.0 No Male 65-69 White Yes Yes Very good 8.0 No No No No 25.11 No No No 5.0 5.0 No Female 65-69 Black No Yes Good 7.0 No No No No 20